In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import dgl
from dgl.nn import ChebConv
import networkx as nx
import networkx.algorithms.community as nx_comm
import numpy as np
import pandas as pd
import numpy.linalg as alg
import os
from tqdm import tqdm
from functools import reduce
import argparse


def node_connects_cluster(node):
    return set(map(lambda x: inverse_cluster_dict[x], list(g[node]))).union(set([inverse_cluster_dict[node]]))


def po_linear_model(graph, alpha=1, beta=1, sigma=0.1, hete=0.5, gamma=2):    
    hete = 0.5
    for i in graph.nodes:
        graph.nodes[i]["y"] = alpha + beta * graph.nodes[i]["z"] + sigma * np.random.normal() +  gamma * sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]])/graph.degree[i]  

def po_multiplicative_model(graph, alpha=1, sigma=0.1, delta=1, gamma=1): 
    for i in graph.nodes:
        graph.nodes[i]["y"] = ( (alpha + sigma * np.random.normal()) * graph.degree[i]/avg_deg )  *  (1 + delta * graph.nodes[i]["z"] + gamma * sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]]) / len(graph[i]) )


DGL backend not selected or invalid.  Assuming PyTorch for now.
/root/miniconda3/envs/myconda/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Setting the default backend to "pytorch". You can change it in the ~/.dgl/config.json file or export the DGLBACKEND environment variable.  Valid options are: pytorch, mxnet, tensorflow (all lowercase)


In [2]:

path = 'Dataset/socfb-Stanford3.mtx'

df = pd.read_table(path, skiprows=1, names = ["source", "target"], sep=" ")
g = nx.from_pandas_edgelist(df)

# calculate basic elements
num_nodes = g.number_of_nodes()
num_edges = g.number_of_edges()
degs = [g.degree[i] for i in g.nodes]
avg_deg = sum(degs)/len(degs)

res = 10


# clustering
# generally, we fix the outcome of clustering
clusters = nx_comm.louvain_communities(g, seed = 10, resolution=res)
clusters = sorted(clusters, key = len, reverse=True)
cluster_sizes = list(map(len, clusters))
num_cluster = len(clusters)

# dict: from node to its cluster
inverse_cluster_dict = {
    node: cl for cl in range(num_cluster) for node in clusters[cl]
}

# dict: from node to its connected cluster
node_to_connected_clusters = {
    node: node_connects_cluster(node) for node in range(1, num_nodes + 1)
}


for i in g.nodes:
    g.nodes[i]["n_cl"] = len(node_to_connected_clusters[i])
    g.nodes[i]["deg"] = g.degree[i]

rev_cluster_sizes = cluster_sizes[::-1]
rev_clusters = clusters[::-1]
rev_cluster_sizes = np.array(rev_cluster_sizes)


In [3]:
dgl_G = dgl.from_networkx(g)

In [4]:
ramps = [0.02, 0.05, 0.1, 0.25, 0.5]
repeat_num = 1000

In [5]:

class GCN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = dgl.nn.ChebConv(2, 16, 2)
        self.conv2 = dgl.nn.ChebConv(16, 16, 1)
        self.conv3 = dgl.nn.ChebConv(16, 1, 1)

        
    def forward(self, g, features):
        x = self.conv1(g, features)
        x = self.conv2(g, x)
        x = self.conv3(g, x)
        return x
        

In [6]:
# cluster-level 



GATE_hat_list = np.zeros((repeat_num, len(ramps)))

     
for seed in tqdm(range(repeat_num)):
    
    np.random.seed(seed)     
    rollout_index = np.random.uniform(0, 1, size=(num_cluster,))   
    
    for num_step in range(len(ramps)): 
        print(f"Seed: {seed}")
        torch.manual_seed(2)
        p_list = ramps[num_step:]        
        g_feat_list = []
        y_list = []
        
        for p in p_list:            
            tr_clusters = np.arange(num_cluster)[rollout_index<np.quantile(rollout_index, p)]            
            tr_units = reduce(lambda x, y: x.union(y), [clusters[i] for i in tr_clusters])  
                        
            nx.set_node_attributes(g, 0, "z")
            nx.set_node_attributes(g, {unit:1 for unit in tr_units}, "z")
            
            po_multiplicative_model(g, gamma=1)
            g_feat_list.append(torch.tensor([[g.nodes[n]['z'], g.nodes[n]['deg']] for n in g.nodes], dtype=torch.float))
            y_list.append(torch.tensor([[g.nodes[n]['y']] for n in g.nodes], dtype=torch.float).reshape(-1))
    
        # Instantiate the model and optimizer
        model = GCN()
        optimizer = torch.optim.Adam(model.parameters(), lr=0.004)
            
        # Train the model
        for epoch in range(400):
            for i in range(len(p_list)):
                model.train()
                optimizer.zero_grad()
                out = model(dgl_G, g_feat_list[i])
                loss = F.mse_loss(out.squeeze(), y_list[i])  
                loss.backward()
                optimizer.step()
            
                if epoch % 50 == 0:
                    print(f'Epoch {epoch}, Treat Prop: {p_list[i]:.2f}, Loss: {loss:.4f}')
    
        print(loss.item())
        g_feat = g_feat_list[0]
    
        g_feat[:,0] = 0
        global_control_pred = model(dgl_G, g_feat).detach().numpy()
    
        g_feat[:,0] = 1
        global_treat_pred = model(dgl_G, g_feat).detach().numpy()
    
        GATE_hat = global_treat_pred.mean() - global_control_pred.mean()
    
        GATE_hat_list[seed, num_step] = GATE_hat
        
    torch.save(GATE_hat_list, "Result/Multiplicative_CR_cluster.pkl")


  0%|          | 0/1000 [00:00<?, ?it/s]

Seed: 0


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/dgl/nn/pytorch/conv/chebconv.py:108: DGLWarning: lambda_max is not provided, using default value of 2.  Please use dgl.laplacian_lambda_max to compute the eigenvalues.
  dgl_warning(


Epoch 0, Treat Prop: 0.02, Loss: 4.5098
Epoch 0, Treat Prop: 0.05, Loss: 0.6581
Epoch 0, Treat Prop: 0.10, Loss: 1.5278
Epoch 0, Treat Prop: 0.25, Loss: 3.8210
Epoch 0, Treat Prop: 0.50, Loss: 7.9875
Epoch 50, Treat Prop: 0.02, Loss: 0.3001
Epoch 50, Treat Prop: 0.05, Loss: 0.3165
Epoch 50, Treat Prop: 0.10, Loss: 0.3017
Epoch 50, Treat Prop: 0.25, Loss: 0.5701
Epoch 50, Treat Prop: 0.50, Loss: 1.8399
Epoch 100, Treat Prop: 0.02, Loss: 0.2353
Epoch 100, Treat Prop: 0.05, Loss: 0.2753
Epoch 100, Treat Prop: 0.10, Loss: 0.2168
Epoch 100, Treat Prop: 0.25, Loss: 0.4162
Epoch 100, Treat Prop: 0.50, Loss: 1.3503
Epoch 150, Treat Prop: 0.02, Loss: 0.1956
Epoch 150, Treat Prop: 0.05, Loss: 0.1913
Epoch 150, Treat Prop: 0.10, Loss: 0.0921
Epoch 150, Treat Prop: 0.25, Loss: 0.3405
Epoch 150, Treat Prop: 0.50, Loss: 0.7071
Epoch 200, Treat Prop: 0.02, Loss: 0.1385
Epoch 200, Treat Prop: 0.05, Loss: 0.1176
Epoch 200, Treat Prop: 0.10, Loss: 0.0663
Epoch 200, Treat Prop: 0.25, Loss: 0.2200
Epoch 2

  0%|          | 1/1000 [00:41<11:29:43, 41.42s/it]

...

0.12841488420963287
Seed: 998
Epoch 0, Treat Prop: 0.02, Loss: 4.3670
Epoch 0, Treat Prop: 0.05, Loss: 0.6718
Epoch 0, Treat Prop: 0.10, Loss: 1.5330
Epoch 0, Treat Prop: 0.25, Loss: 3.8164
Epoch 0, Treat Prop: 0.50, Loss: 7.1657
Epoch 50, Treat Prop: 0.02, Loss: 0.2828
Epoch 50, Treat Prop: 0.05, Loss: 0.3224
Epoch 50, Treat Prop: 0.10, Loss: 0.3027
Epoch 50, Treat Prop: 0.25, Loss: 0.5527
Epoch 50, Treat Prop: 0.50, Loss: 1.5562
Epoch 100, Treat Prop: 0.02, Loss: 0.2033
Epoch 100, Treat Prop: 0.05, Loss: 0.3261
Epoch 100, Treat Prop: 0.10, Loss: 0.2458
Epoch 100, Treat Prop: 0.25, Loss: 0.3633
Epoch 100, Treat Prop: 0.50, Loss: 1.1031
Epoch 150, Treat Prop: 0.02, Loss: 0.1157
Epoch 150, Treat Prop: 0.05, Loss: 0.1982
Epoch 150, Treat Prop: 0.10, Loss: 0.1603
Epoch 150, Treat Prop: 0.25, Loss: 0.1654
Epoch 150, Treat Prop: 0.50, Loss: 0.3499
Epoch 200, Treat Prop: 0.02, Loss: 0.0634
Epoch 200, Treat Prop: 0.05, Loss: 0.0739
Epoch 200, Treat Prop: 0.10, Loss: 0.0640
Epoch 200, Treat Pr

100%|█████████▉| 999/1000 [10:32:50<00:35, 35.30s/it]

0.1866726279258728
Seed: 999
Epoch 0, Treat Prop: 0.02, Loss: 4.4483
Epoch 0, Treat Prop: 0.05, Loss: 0.6726
Epoch 0, Treat Prop: 0.10, Loss: 1.5498
Epoch 0, Treat Prop: 0.25, Loss: 3.6239
Epoch 0, Treat Prop: 0.50, Loss: 7.4574
Epoch 50, Treat Prop: 0.02, Loss: 0.2649
Epoch 50, Treat Prop: 0.05, Loss: 0.2905
Epoch 50, Treat Prop: 0.10, Loss: 0.3011
Epoch 50, Treat Prop: 0.25, Loss: 0.5096
Epoch 50, Treat Prop: 0.50, Loss: 1.6804
Epoch 100, Treat Prop: 0.02, Loss: 0.1835
Epoch 100, Treat Prop: 0.05, Loss: 0.2166
Epoch 100, Treat Prop: 0.10, Loss: 0.1904
Epoch 100, Treat Prop: 0.25, Loss: 0.3487
Epoch 100, Treat Prop: 0.50, Loss: 1.1696
Epoch 150, Treat Prop: 0.02, Loss: 0.0652
Epoch 150, Treat Prop: 0.05, Loss: 0.0954
Epoch 150, Treat Prop: 0.10, Loss: 0.0956
Epoch 150, Treat Prop: 0.25, Loss: 0.1543
Epoch 150, Treat Prop: 0.50, Loss: 0.4757
Epoch 200, Treat Prop: 0.02, Loss: 0.0474
Epoch 200, Treat Prop: 0.05, Loss: 0.0674
Epoch 200, Treat Prop: 0.10, Loss: 0.0774
Epoch 200, Treat Pro

100%|██████████| 1000/1000 [10:33:25<00:00, 38.01s/it]

0.19422338902950287


array([[1.87950706, 1.70982361, 1.78494787, 1.79924452, 1.53536904],
       [1.79088247, 1.74497986, 1.77617741, 1.78228199, 1.45078003],
       [1.7166729 , 1.69054794, 1.75266743, 1.76328743, 1.44348931],
       [1.70705831, 1.70737147, 1.75053096, 1.7739917 , 1.30893612],
       [1.82307577, 1.70411325, 1.713714  , 1.75858212, 1.45008981]])